In [10]:
import json
import numpy as np
from pathlib import Path
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical

from tensorflow.keras.models import Model
from tensorflow.keras.layers import (
    Input,
    Embedding,
    LSTM,
    Concatenate,
    Dense,
    TimeDistributed,
)
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.metrics import classification_report

In [11]:
# load dataset
with open("new_dataset.json", encoding="utf-8") as f:
    raw_data = json.load(f)

print(len(raw_data))
tokens = [[t.lower().strip() for t in item["tokens"]] for item in raw_data]

ner_tags = [item["ner"] for item in raw_data]
srl_tags = [item["srl"] for item in raw_data]
questions = [[token.lower().strip() for token in item["question"]] for item in raw_data]
answers = [[token.lower().strip() for token in item["answer"]] for item in raw_data]

print(questions)

types = [item["type"] for item in raw_data]


5000
[['___', 'cipta', '©', '201', 'pada', 'kementerian', 'pendidikan', 'dan', 'kebudayaan', 'dilindung', 'i', 'undang-undang', 'disklaimer', 'buku', 'ini', 'merupakan', 'buku', 'siswa', 'yang', 'dipersiapkan', 'pemerintah', 'dalam', 'rangka', 'implementasi', 'kurikulum', '2013'], ['apakah', 'buku', 'siswa', 'ini', 'disusun', 'dan', 'ditelaah', 'oleh', 'berbagai', 'pihak', 'di', 'bawah', 'koordinasi', 'kementerian', 'pendidikandan', 'kebudayaan,', 'dan', 'dipergunakan', 'dalam', 'tahap', 'awal', 'penerapan', 'kurikulum', '2013.', '?'], ['___', 'ini', 'merupakan', 'ﬁdokumen', 'hidupﬂ', 'yang', 'senantiasa', 'diperbaiki', 'diperbaharui', 'dan', 'dimutakhirkan', 'sesuai', 'dengan', 'dinamika', 'kebutuhan', 'dan', 'perubahan', 'zaman'], ['apakah', 'masukan', 'dari', 'berbagai', 'kalangan', 'yang', 'dialamatkan', 'kepada', 'penulis', 'dan', 'laman', 'http://buku.kemdikbud.go.id', 'atau', 'melalui', 'email', 'buku@kemdikbud.go.iddiharapkan', 'dapat', 'meningkatkan', 'kualitas', 'buku', 'ini.

In [12]:
# tokenize
token_tok = Tokenizer(lower=False, oov_token="UNK")
token_ner = Tokenizer(lower=False)
token_srl = Tokenizer(lower=False)
token_q = Tokenizer(lower=False)
token_a = Tokenizer(lower=False)
token_type = Tokenizer(lower=False)

token_tok.fit_on_texts(tokens)
token_ner.fit_on_texts(ner_tags)
token_srl.fit_on_texts(srl_tags)
token_q.fit_on_texts(questions)
token_a.fit_on_texts(answers)
token_type.fit_on_texts(types)


maxlen = 20

In [13]:

X_tok = pad_sequences(
    token_tok.texts_to_sequences(tokens), padding="post", maxlen=maxlen
)
X_ner = pad_sequences(
    token_ner.texts_to_sequences(ner_tags), padding="post", maxlen=maxlen
)
X_srl = pad_sequences(
    token_srl.texts_to_sequences(srl_tags), padding="post", maxlen=maxlen
)
y_q = pad_sequences(token_q.texts_to_sequences(questions), padding="post", maxlen=maxlen)
y_a = pad_sequences(token_a.texts_to_sequences(answers), padding="post", maxlen=maxlen)

print(types)
y_type = [seq[0] for seq in token_type.texts_to_sequences(types)]  # list of int
y_type = to_categorical(np.array(y_type) - 1, num_classes=len(token_type.word_index))



['isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', 'true_false', 'isian', '

In [14]:
X_tok_train, X_tok_test, X_ner_train, X_ner_test, X_srl_train, X_srl_test, \
y_q_train, y_q_test, y_a_train, y_a_test, y_type_train, y_type_test = train_test_split(
    X_tok, X_ner, X_srl, y_q, y_a, y_type, test_size=0.2, random_state=42
)

X_train = [X_tok_train, X_ner_train, X_srl_train]
X_test = [X_tok_test, X_ner_test, X_srl_test]

In [15]:

inp_tok = Input(shape=(None,), name="tok_input")
inp_ner = Input(shape=(None,), name="ner_input")
inp_srl = Input(shape=(None,), name="srl_input")

emb_tok = Embedding(input_dim=len(token_tok.word_index) + 1, output_dim=128)(inp_tok)
emb_ner = Embedding(input_dim=len(token_ner.word_index) + 1, output_dim=16)(inp_ner)
emb_srl = Embedding(input_dim=len(token_srl.word_index) + 1, output_dim=16)(inp_srl)

# emb_tok = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_tok)
# emb_ner = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_ner)
# emb_srl = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_srl)

merged = Concatenate()([emb_tok, emb_ner, emb_srl])

x = LSTM(256, return_sequences=True)(merged)

out_question = TimeDistributed(Dense(len(token_q.word_index) + 1, activation="softmax"), name="question_output")(x)
out_answer = TimeDistributed(Dense(len(token_a.word_index) + 1, activation="softmax"), name="answer_output")(x)
out_type = Dense(len(token_type.word_index), activation="softmax", name="type_output")(
    x[:, 0, :]
)  # gunakan step pertama

model = Model(
    inputs=[inp_tok, inp_ner, inp_srl], outputs=[out_question, out_answer, out_type]
)
model.compile(
    optimizer="adam",
    loss={
        "question_output": "sparse_categorical_crossentropy",
        "answer_output": "sparse_categorical_crossentropy",
        "type_output": "categorical_crossentropy",
    },
    metrics={
        "question_output": "accuracy",
        "answer_output": "accuracy",
        "type_output": "accuracy",
    },
)

model.summary()

# ----------------------------------------------------------------------------
# 5. TRAINING
# ----------------------------------------------------------------------------
model.fit(
    X_train,
    {
        "question_output": np.expand_dims(y_q_train, -1),
        "answer_output": np.expand_dims(y_a_train, -1),
        "type_output": y_type_train,
    },
    batch_size=32,
    epochs=30,
    validation_split=0.1,
    callbacks=[EarlyStopping(patience=3, restore_best_weights=True)],
)

import pickle


model.save("lstm_qg.keras")
with open("tokenizers.pkl", "wb") as f:
    pickle.dump({
        "token": token_tok,
        "ner": token_ner,
        "srl": token_srl,
        "question": token_q,
        "answer": token_a,
        "type": token_type
    }, f)



Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ tok_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ srl_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_3         │ (None, None, 128) │  1,515,264 │ tok_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_4         │ (None, None, 16)  │         80 │ ner_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_5         │ (None, None, 16)  │         80 │ srl_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_1       │ (None, None, 160) │          0 │ embedding_3[0][0… │
│ (Concatenate)       │                   │            │ embedding_4[0][0… │
│                     │                   │            │ embedding_5[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_1 (LSTM)       │ (None, None, 256) │    427,008 │ concatenate_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ get_item_1          │ (None, 256)       │          0 │ lstm_1[0][0]      │
│ (GetItem)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_output     │ (None, None,      │  2,582,850 │ lstm_1[0][0]      │
│ (TimeDistributed)   │ 10050)            │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ answer_output       │ (None, None, 683) │    175,531 │ lstm_1[0][0]      │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ type_output (Dense) │ (None, 3)         │        771 │ get_item_1[0][0]  │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 4,701,584 (17.94 MB)

 Trainable params: 4,701,584 (17.94 MB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/30
113/113 ━━━━━━━━━━━━━━━━━━━━ 22s 180ms/step - answer_output_accuracy: 0.9047 - answer_output_loss: 2.0928 - loss: 9.7376 - question_output_accuracy: 0.3309 - question_output_loss: 6.7415 - type_output_accuracy: 0.6032 - type_output_loss: 0.9032 - val_answer_output_accuracy: 0.9620 - val_answer_output_loss: 0.1983 - val_loss: 5.8041 - val_question_output_accuracy: 0.3909 - val_question_output_loss: 4.9735 - val_type_output_accuracy: 0.5975 - val_type_output_loss: 0.6284
Epoch 2/30
113/113 ━━━━━━━━━━━━━━━━━━━━ 20s 179ms/step - answer_output_accuracy: 0.9635 - answer_output_loss: 0.1866 - loss: 5.2670 - question_output_accuracy: 0.4004 - question_output_loss: 4.4942 - type_output_accuracy: 0.6476 - type_output_loss: 0.5861 - val_answer_output_accuracy: 0.9655 - val_answer_output_loss: 0.1788 - val_loss: 5.0597 - val_question_output_accuracy: 0.4481 - val_question_output_loss: 4.2631 - val_type_output_accuracy: 0.5900 - val_type_output_loss: 0.6189
Epoch 3/30
113/113 ━━━━━━━━━━━

In [16]:

def token_level_accuracy(y_true, y_pred):
    correct = 0
    total = 0
    for true_seq, pred_seq in zip(y_true, y_pred):
        for t, p in zip(true_seq, pred_seq):
            if t != 0:  # ignore padding
                total += 1
                if t == p:
                    correct += 1
    return correct / total if total > 0 else 0


# Predict on test set
y_pred_q, y_pred_a, y_pred_type = model.predict(X_test)

# Decode predictions to class indices
y_pred_q = np.argmax(y_pred_q, axis=-1)
y_pred_a = np.argmax(y_pred_a, axis=-1)
y_pred_type = np.argmax(y_pred_type, axis=-1)
y_true_type = np.argmax(y_type_test, axis=-1)

# Calculate token-level accuracy
acc_q = token_level_accuracy(y_q_test, y_pred_q)
acc_a = token_level_accuracy(y_a_test, y_pred_a)

# Type classification report
report_type = classification_report(y_true_type, y_pred_type, zero_division=0)

# Print Results
print("\n=== Akurasi Detail ===")
print(f"Question Accuracy (Token-level): {acc_q:.1f}")
print(f"Answer Accuracy (Token-level)  : {acc_a:.1f}")
print(f"Type Accuracy (Class-level)   : {np.mean(y_true_type == y_pred_type):.2f}")
print("\n=== Classification Report (TYPE) ===")
print(report_type)

32/32 ━━━━━━━━━━━━━━━━━━━━ 2s 43ms/step

=== Akurasi Detail ===
Question Accuracy (Token-level): 0.2
Answer Accuracy (Token-level)  : 0.4
Type Accuracy (Class-level)   : 0.61

=== Classification Report (TYPE) ===
              precision    recall  f1-score   support

           0       0.66      0.74      0.70       614
           1       0.49      0.41      0.45       386

    accuracy                           0.61      1000
   macro avg       0.58      0.57      0.57      1000
weighted avg       0.60      0.61      0.60      1000



In [17]:

# flat_true_a, flat_pred_a = flatten_valid(y_a_test, y_pred_a_class)
# print("\n=== Classification Report: ANSWER ===")
# print(classification_report(flat_true_a, flat_pred_a))


In [18]:

# print("\n=== Classification Report: TYPE ===")
# print(classification_report(y_true_type_class, y_pred_type_class))